<a href="https://colab.research.google.com/github/amberlynnk/PortfolioProjects/blob/main/Interactive_Phoenix_Crime_Map_with_basemap_attached.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np
!pip install geopandas;
import geopandas as gpd
from shapely.geometry import shape

from bokeh.io import output_file, show,output_notebook
from bokeh.models import ColumnDataSource,ColorBar,HoverTool
from bokeh.transform import linear_cmap
from bokeh.plotting import figure
from bokeh.palettes import Spectral6

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 16.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.1/16.1 MB 43.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 13.3 MB/s eta 0:00:00


In [4]:
phx_crimes = gpd.read_file("phoenix_crime_counts.shp")


In [5]:
output_notebook()


In [6]:
def gpd_bokeh(df):
    """Convert geometries from geopandas to bokeh format"""
    nan = float('nan')
    lons = []
    lats = []
    for i,shape in enumerate(df.geometry.values):
        if shape.geom_type == 'MultiPolygon':
            gx = []
            gy = []
            ng = len(shape.geoms) - 1
            for j,member in enumerate(shape.geoms):
                xy = np.array(list(member.exterior.coords))
                xs = xy[:,0].tolist()
                ys = xy[:,1].tolist()
                gx.extend(xs)
                gy.extend(ys)
                if j < ng:
                    gx.append(nan)
                    gy.append(nan)
            lons.append(gx)
            lats.append(gy)

        else:     
            xy = np.array(list(shape.exterior.coords))
            xs = xy[:,0].tolist()
            ys = xy[:,1].tolist()
            lons.append(xs)
            lats.append(ys) 

    return lons,lats

In [7]:
phx_crimes.head()


ZCTA5CE10 GEOID10 CLASSFP10 MTFCC10 FUNCSTAT10   ALAND10  AWATER10  \
0     85019   85019        B5   G6350          S   9713482     16770   
1     85020   85020        B5   G6350          S  23027500     65264   
2     85021   85021        B5   G6350          S  17419881     74879   
3     85022   85022        B5   G6350          S  24230483      4009   
4     85023   85023        B5   G6350          S  18927812     18972   

    INTPTLAT10    INTPTLON10  Zipcode    ZIP  INC NUMBER  \
0  +33.5088785  -112.1445137    85019  85019        1439   
1  +33.5673508  -112.0535909    85020  85020        1510   
2  +33.5594209  -112.0928747    85021  85021        2372   
3  +33.6272400  -112.0484143    85022  85022        1616   
4  +33.6341180  -112.0931632    85023  85023        1806   

                                            geometry  
0  POLYGON ((-112.15154 33.51432, -112.15153 33.5...  
1  POLYGON ((-112.03919 33.59392, -112.03904 33.5...  
2  POLYGON ((-112.11569 33.56233, -112.11609 33.5...  
3  POLYGON ((-112.07416 33.64750, -112.07416 33.6...  
4  POLYGON ((-112.11518 33.64381, -112.11501 33.6...

In [8]:
lons, lats = gpd_bokeh(phx_crimes)
source = ColumnDataSource(data=dict(
    	x=lons, 
    	y=lats,
        zipcode = phx_crimes['Zipcode'],
        crime_counts = phx_crimes['INC NUMBER']))

In [9]:
color_mapper = linear_cmap(field_name='crime_counts', palette=Spectral6 ,
                           low=min(phx_crimes['INC NUMBER']) ,
                           high=max(phx_crimes['INC NUMBER']))
TOOLS = "pan,wheel_zoom,reset,hover,save"


In [10]:
map = figure(plot_width=800, plot_height=600,title="Phoenix Crime Map", tools=TOOLS,)
map.patches('x', 'y', source=source, line_color="white", line_width=0.1, color=color_mapper)

map.select_one(HoverTool).tooltips = [
    ('Crime_counts', '@crime_counts'),
    ('Zipcode', '@zipcode')
]

color_bar = ColorBar(color_mapper=color_mapper['transform'], width=16, location=(0,0))
map.add_layout(color_bar, 'right')


In [11]:
output_file("phoenix_crime.html")
show(map)

In [12]:
import folium


In [13]:
folium.Map(location=[33.4255, -111.9400])


In [14]:
help(folium.Map)


Help on class Map in module folium.folium:

class Map(folium.elements.JSCSSMixin, branca.element.MacroElement)
 |  Map(location=None, width='100%', height='100%', left='0%', top='0%', position='relative', tiles='OpenStreetMap', attr=None, min_zoom=0, max_zoom=18, zoom_start=10, min_lat=-90, max_lat=90, min_lon=-180, max_lon=180, max_bounds=False, crs='EPSG3857', control_scale=False, prefer_canvas=False, no_touch=False, disable_3d=False, png_enabled=False, zoom_control=True, **kwargs)
 |  
 |  Create a Map with Folium and Leaflet.js
 |  
 |  Generate a base map of given width and height with either default
 |  tilesets or a custom tileset URL. The following tilesets are built-in
 |  to Folium. Pass any of the following to the "tiles" keyword:
 |  
 |      - "OpenStreetMap"
 |      - "Mapbox Bright" (Limited levels of zoom for free tiles)
 |      - "Mapbox Control Room" (Limited levels of zoom for free tiles)
 |      - "Stamen" (Terrain, Toner, and Watercolor)
 |      - "Cloudmade" (Must

In [15]:
asu = folium.Map(
    location=[33.4200, -111.9350],
    tiles='Stamen Toner',
    zoom_start=15,
    width=1000, 
    height=400
)
asu

In [16]:
folium.Marker([33.419536, -111.937902], popup='<i>COOR Hall</i>').add_to(asu)
folium.Marker([33.415721, -111.932012], popup='<b>Gym</b>').add_to(asu)
asu

In [17]:
phx_crimes.crs


<Geographic 2D CRS: EPSG:4269>
Name: NAD83
Axis Info [ellipsoidal]:
- Lat[north]: Geodetic latitude (degree)
- Lon[east]: Geodetic longitude (degree)
Area of Use:
- name: North America - onshore and offshore: Canada - Alberta; British Columbia; Manitoba; New Brunswick; Newfoundland and Labrador; Northwest Territories; Nova Scotia; Nunavut; Ontario; Prince Edward Island; Quebec; Saskatchewan; Yukon. Puerto Rico. United States (USA) - Alabama; Alaska; Arizona; Arkansas; California; Colorado; Connecticut; Delaware; Florida; Georgia; Hawaii; Idaho; Illinois; Indiana; Iowa; Kansas; Kentucky; Louisiana; Maine; Maryland; Massachusetts; Michigan; Minnesota; Mississippi; Missouri; Montana; Nebraska; Nevada; New Hampshire; New Jersey; New Mexico; New York; North Carolina; North Dakota; Ohio; Oklahoma; Oregon; Pennsylvania; Rhode Island; South Carolina; South Dakota; Tennessee; Texas; Utah; Vermont; Virginia; Washington; West Virginia; Wisconsin; Wyoming. US Virgin Islands. British Virgin Islands

In [18]:
{'init': 'epsg:4269'}


{'init': 'epsg:4269'}

In [19]:
phx_crimes_json = phx_crimes.to_crs(epsg='4326').to_json()


In [20]:
crime_map = folium.Map(location=[33.4255, -111.9400], zoom_start=9)


In [21]:
folium.Choropleth(
    geo_data=phx_crimes_json,
    name='Phoenix Crime Counts', # 
    data=phx_crimes, #Our GeoDataFrame
    columns=['Zipcode','INC NUMBER'], #
    key_on='feature.properties.{}'.format('Zipcode'), #we need to specify a unique key for each zipcode
    fill_color='RdBu_r', #fill color, here I'm using blue to red
    fill_opacity=0.7, # opacity of the polygon fill color
    line_opacity=0.2, # opacity of the boundary line
    legend_name='counts', #legend name
    highlight = True, #Hover to highlight
    control = True
).add_to(crime_map)

crime_map


In [22]:
folium.LayerControl().add_to(crime_map)
crime_map


In [23]:
crime_map.save('phx_crime_map_folium.html')
